In [1]:
import pandas as pd
import numpy as np
import json
import csv
#1.确定这几个数据都是干什么的
swiping_card_dataframe = pd.read_csv('./bus_swiping_card_info1.csv')
card_info_dataframe = pd.read_csv('./card_info.csv')
bus_swip_dataframe = pd.read_excel('公交数据.xlsx',sheet_name='刷卡数据',header=0,engine='openpyxl')
bus_station_dataframe = pd.read_excel('公交数据.xlsx',sheet_name='站点数据',header=0,engine='openpyxl')
#swiping_card_dataframe ： 每次刷卡的信息：几号线，第几站，车辆的id，刷卡的id，刷卡的时间
#card_info_dataframe ： 每次刷卡的信息：几号线，第几站，车辆的id，刷卡的id，刷卡的时间也是上面的信息，但是时间是去年的。
#用去年的时间的同比数据，去预测今年的同比数据，看是否一致，如果一致，说明经济发展没有变化，如果变大，说明经济好转
#bus_swip_dataframe ：一天的统计信息：各条线路、各个站点的刷卡数量信息
#bus_station_dataframe ： 站点的统计信息：各个站点的经纬度

In [2]:
# 从文件中读取字典
with open('./datas/id_2_station.json', 'r') as file:
    id_2_station = json.load(file)
# 将字典保存到文件中
with open('./datas/station_2_id.json', 'r') as file:
    station_2_id = json.load(file)

In [3]:
bus_station_dataframe
#这个表里面只包含了线路和站点的关系，
#可以推出，线路有哪些站点，站点过哪些线路
#可以推出路段过哪些线路，线路过哪些路段。
#但是不能找到路段与公交的关系。
line_station_number_sequen_dataframe = \
bus_station_dataframe.groupby(['line_identity','station_number']).agg({'station_name':list,'station_identity':list}).reset_index()
line_station_number_sequen_dataframe['length'] = line_station_number_sequen_dataframe['station_identity'].apply(lambda x:len(x))
line_station_number_sequen_dataframe
#首先构建路段到线路的映射字典。
road_section_2_lines = {}
#逐线路的添加路段
for row_index in range(len(line_station_number_sequen_dataframe)):
    line_station_number_sequen_dataframe_row = line_station_number_sequen_dataframe[row_index:row_index+1]
    line_identity:int = line_station_number_sequen_dataframe_row['line_identity'].values[0]
    stations_list:list = line_station_number_sequen_dataframe_row['station_name'].values[0]
    #print(stations_list)
    for start_order in range(len(stations_list)-1):
        start_station = stations_list[start_order]
        end_station = stations_list[start_order+1]
        start_station_order = station_2_id[start_station]
        end_station_order = station_2_id[end_station]
        road_section_2_lines_key = f"{start_station_order}_{end_station_order}"
        if road_section_2_lines_key in road_section_2_lines:
            road_section_2_lines[road_section_2_lines_key].append(line_identity)
        else:
            road_section_2_lines[road_section_2_lines_key]=[line_identity]
road_section_2_lines
#此表信息彻底被用完。

{'806_508': [1,
  2,
  17,
  18,
  24,
  65,
  78,
  237,
  253,
  272,
  1012,
  1018,
  1024,
  6004,
  6008],
 '508_633': [1,
  2,
  6,
  18,
  24,
  29,
  65,
  78,
  237,
  253,
  272,
  308,
  1012,
  1014,
  1018,
  1024,
  4300,
  6003,
  6008],
 '633_1208': [1, 24, 29, 44, 253, 272, 308, 1012, 1018, 8068],
 '1208_387': [1, 1012],
 '387_349': [1,
  8,
  9,
  11,
  17,
  26,
  45,
  48,
  54,
  67,
  84,
  249,
  264,
  810,
  1009,
  1012,
  1013,
  1014,
  1019,
  6006,
  8025],
 '349_128': [1, 7, 8, 19, 30, 48, 67, 249, 264, 6010, 6014],
 '128_216': [1, 7, 8, 19, 30, 37, 48, 62, 249, 264, 6010, 6014],
 '216_263': [1, 30, 62, 6010],
 '263_261': [1,
  10,
  22,
  27,
  33,
  51,
  66,
  248,
  260,
  311,
  314,
  316,
  320,
  1020,
  6007],
 '261_1414': [1,
  10,
  16,
  22,
  27,
  33,
  72,
  77,
  248,
  260,
  282,
  311,
  314,
  316,
  320,
  1020,
  6007],
 '1414_1414': [1, 2, 10, 12, 16, 22, 23, 41, 53],
 '1414_555': [1, 41, 209, 238, 8026],
 '555_987': [1,
  3,
  28,

In [4]:
lines_list = line_station_number_sequen_dataframe['line_identity'].values
lines_list 

array([    1,     2,     3,     4,     5,     6,     7,     8,     9,
          10,    11,    12,    13,    14,    15,    16,    17,    18,
          19,    20,    21,    22,    23,    24,    25,    26,    27,
          28,    29,    30,    31,    32,    33,    34,    35,    36,
          37,    38,    39,    40,    41,    42,    43,    44,    45,
          46,    47,    48,    49,    50,    51,    52,    53,    54,
          55,    56,    57,    58,    59,    60,    61,    62,    63,
          64,    65,    66,    67,    68,    69,    70,    71,    72,
          73,    74,    75,    76,    77,    78,    79,    80,    81,
          82,    83,    84,    85,    86,    87,   201,   202,   203,
         204,   205,   206,   207,   208,   209,   210,   211,   212,
         213,   214,   215,   216,   217,   218,   219,   220,   221,
         222,   223,   224,   225,   226,   227,   228,   229,   230,
         231,   232,   233,   234,   235,   236,   237,   238,   239,
         240,   241,

In [5]:
line_2_id = {}
id_2_line = {}
for line_id in range(len(lines_list)):
    line_2_id[lines_list[line_id]] = line_id
    id_2_line[line_id] = lines_list[line_id]
id_2_line,line_2_id

({0: 1,
  1: 2,
  2: 3,
  3: 4,
  4: 5,
  5: 6,
  6: 7,
  7: 8,
  8: 9,
  9: 10,
  10: 11,
  11: 12,
  12: 13,
  13: 14,
  14: 15,
  15: 16,
  16: 17,
  17: 18,
  18: 19,
  19: 20,
  20: 21,
  21: 22,
  22: 23,
  23: 24,
  24: 25,
  25: 26,
  26: 27,
  27: 28,
  28: 29,
  29: 30,
  30: 31,
  31: 32,
  32: 33,
  33: 34,
  34: 35,
  35: 36,
  36: 37,
  37: 38,
  38: 39,
  39: 40,
  40: 41,
  41: 42,
  42: 43,
  43: 44,
  44: 45,
  45: 46,
  46: 47,
  47: 48,
  48: 49,
  49: 50,
  50: 51,
  51: 52,
  52: 53,
  53: 54,
  54: 55,
  55: 56,
  56: 57,
  57: 58,
  58: 59,
  59: 60,
  60: 61,
  61: 62,
  62: 63,
  63: 64,
  64: 65,
  65: 66,
  66: 67,
  67: 68,
  68: 69,
  69: 70,
  70: 71,
  71: 72,
  72: 73,
  73: 74,
  74: 75,
  75: 76,
  76: 77,
  77: 78,
  78: 79,
  79: 80,
  80: 81,
  81: 82,
  82: 83,
  83: 84,
  84: 85,
  85: 86,
  86: 87,
  87: 201,
  88: 202,
  89: 203,
  90: 204,
  91: 205,
  92: 206,
  93: 207,
  94: 208,
  95: 209,
  96: 210,
  97: 211,
  98: 212,
  99: 213,
  100:

In [6]:
for key in road_section_2_lines.keys():
    print(key)
    print(road_section_2_lines[key])
    break

806_508
[1, 2, 17, 18, 24, 65, 78, 237, 253, 272, 1012, 1018, 1024, 6004, 6008]


In [7]:
#获取0929的刷卡数据
#从card_info_dataframe中找出所有用户一天内的od对信息
card_info_dataframe['custom_day'] = card_info_dataframe['custom_time'].apply(lambda x:x.split(' ')[0])
card_info_dataframe['custom_precise_time'] = card_info_dataframe['custom_time'].apply(lambda x:x.split(' ')[1])
#sum(card_info_dataframe['partitionday']==card_info_dataframe['custom_day'])
#card_info_dataframe
card_info_dataframe.drop(labels=['custom_time','card_type','consume','data_src','data_load_time','partitionday'],axis=1,inplace=True)
card_info_dataframe
day_0929_dataframe = card_info_dataframe[card_info_dataframe['custom_day']=='2023-09-29']
day_0929_dataframe

card_identity  line_identity  car_identity  \
0       0x1FDD5BE63E904A3230A0AE9AA0E40C61             28          7520   
1       0x1FFC5D30D96AE2C4524842A09AA67C44             84          5085   
2       0x65F9DAD54040FBE48972B10F3B6337DC             25          6718   
3       0x747A26B4727A9A3094A1881F29D01510            208          6655   
4       0x81A8FFB4112FDBA4782A4FB50E1C0EE0            204          4472   
...                                    ...            ...           ...   
377159  0x51A33F38105E35D006C03F0694252007             52          5054   
377160  0x5BD2D7FBE1BE24A24AFD4D3ECA27FD3F              1          4662   
377161  0x6D191CC173F9415C1148B434D2F9012E            203          4810   
377162  0x7896A07D162530E734F876D16301EFEB             73          5176   
377163  0xB0187B46B74D40AD0A3974334941981F             52          5010   

        station_identity  custom_day custom_precise_time  
0                     54  2023-09-29            08:59:40  
1                     24  2023-09-29            11:08:22  
2                      4  2023-09-29            08:51:28  
3                      1  2023-09-29            22:32:48  
4                     46  2023-09-29            19:50:37  
...                  ...         ...                 ...  
377159                22  2023-09-29            08:48:38  
377160                 6  2023-09-29            10:33:45  
377161                 5  2023-09-29            14:57:10  
377162                23  2023-09-29            15:08:49  
377163                23  2023-09-29            15:13:59  

[377164 rows x 6 columns]

In [8]:
#按照刷卡id进行聚合
every_user_all_trips_dataframe = \
day_0929_dataframe.groupby('card_identity').agg({'custom_precise_time':list, \
                                                 'line_identity':list, \
                                                 'station_identity':list, \
                                                'car_identity':list},axis=1).reset_index()
every_user_all_trips_dataframe

card_identity  \
0       0x0000163558B8AB77BFF797FEEEE10F01   
1       0x00002316F1F629863FF3E818D0BE265A   
2       0x0000719AE3ECECBABAD0263AF940450F   
3       0x0000D15C7814D19BE81C40B3ED9CA55C   
4       0x00011B99B94B97B1B61531D224E3424B   
...                                    ...   
181185  0xFFFE02778DE233DDA75564C495BD3228   
181186  0xFFFE497646C86E8A616A1D2B4E812A32   
181187  0xFFFF08775F76420FEC1D00E61F601F7B   
181188  0xFFFF1614BC6EA98C0DA00D2C0E4BF167   
181189  0xFFFF28A3FBF5F24F4207DB9117D78F64   

                             custom_precise_time       line_identity  \
0                                     [12:52:32]               [207]   
1                                     [13:59:15]                 [3]   
2                           [19:01:59, 16:55:43]            [40, 46]   
3       [09:26:05, 19:24:18, 16:29:50, 09:20:51]  [207, 202, 5, 204]   
4                                     [10:25:43]                 [7]   
...                                          ...                 ...   
181185                      [15:54:58, 16:20:02]           [238, 41]   
181186                                [16:37:40]                [32]   
181187                                [11:27:00]               [603]   
181188                                [13:40:04]                [35]   
181189                                [16:28:22]                [20]   

       station_identity              car_identity  
0                   [6]                    [3996]  
1                   [4]                    [7265]  
2               [31, 1]              [4483, 3762]  
3        [14, 39, 5, 8]  [7111, 4622, 4786, 4400]  
4                  [31]                    [5014]  
...                 ...                       ...  
181185          [3, 29]              [4975, 6642]  
181186              [1]                    [3920]  
181187              [8]                    [4576]  
181188              [1]                    [4887]  
181189             [18]                    [4330]  

[181190 rows x 5 columns]

In [9]:
day_0929_dataframe

card_identity  line_identity  car_identity  \
0       0x1FDD5BE63E904A3230A0AE9AA0E40C61             28          7520   
1       0x1FFC5D30D96AE2C4524842A09AA67C44             84          5085   
2       0x65F9DAD54040FBE48972B10F3B6337DC             25          6718   
3       0x747A26B4727A9A3094A1881F29D01510            208          6655   
4       0x81A8FFB4112FDBA4782A4FB50E1C0EE0            204          4472   
...                                    ...            ...           ...   
377159  0x51A33F38105E35D006C03F0694252007             52          5054   
377160  0x5BD2D7FBE1BE24A24AFD4D3ECA27FD3F              1          4662   
377161  0x6D191CC173F9415C1148B434D2F9012E            203          4810   
377162  0x7896A07D162530E734F876D16301EFEB             73          5176   
377163  0xB0187B46B74D40AD0A3974334941981F             52          5010   

        station_identity  custom_day custom_precise_time  
0                     54  2023-09-29            08:59:40  
1                     24  2023-09-29            11:08:22  
2                      4  2023-09-29            08:51:28  
3                      1  2023-09-29            22:32:48  
4                     46  2023-09-29            19:50:37  
...                  ...         ...                 ...  
377159                22  2023-09-29            08:48:38  
377160                 6  2023-09-29            10:33:45  
377161                 5  2023-09-29            14:57:10  
377162                23  2023-09-29            15:08:49  
377163                23  2023-09-29            15:13:59  

[377164 rows x 6 columns]

In [10]:
#将下面的操作表示为dataframe操作
#首先丢弃线路不在的。
day_0929_dataframe_in_lines_list = day_0929_dataframe[day_0929_dataframe['line_identity'].isin(lines_list)].reset_index(drop=True)
day_0929_dataframe_in_lines_list
#按照busid进行聚合
day_0929_bus_info_dataframe = \
day_0929_dataframe_in_lines_list.groupby('car_identity').agg({'custom_precise_time':list, \
                                                 'line_identity':set, \
                                                 'station_identity':list, \
                                                'card_identity':list},axis=1).reset_index()
day_0929_bus_info_dataframe

car_identity                                custom_precise_time  \
0             3730                               [18:58:34, 18:58:55]   
1             3732  [07:13:16, 10:58:56, 18:55:56, 10:58:52, 15:12...   
2             3734                                         [17:48:18]   
3             3736  [19:08:33, 15:20:00, 18:24:07, 18:39:17, 15:04...   
4             3737  [08:58:42, 16:19:23, 07:25:40, 08:15:17, 08:10...   
...            ...                                                ...   
1390          7800  [08:22:42, 13:06:23, 09:27:01, 15:29:52, 08:55...   
1391          7801  [11:47:57, 09:50:06, 16:30:44, 18:12:36, 11:28...   
1392          7823  [07:37:52, 13:59:52, 13:02:56, 11:42:13, 16:04...   
1393         15019  [09:40:52, 12:26:44, 15:42:05, 12:35:19, 15:42...   
1394        207578                               [11:01:28, 08:08:22]   

     line_identity                                   station_identity  \
0           {4601}                                           [37, 37]   
1            {291}  [9, 19, 55, 19, 33, 32, 36, 45, 53, 3, 38, 3, ...   
2           {4601}                                               [37]   
3            {256}  [22, 45, 1, 7, 41, 11, 3, 10, 47, 4, 58, 58, 2...   
4            {256}  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
...            ...                                                ...   
1390         {602}  [2, 23, 31, 23, 18, 2, 19, 7, 18, 18, 18, 6, 1...   
1391         {602}  [18, 18, 18, 6, 7, 23, 24, 7, 18, 1, 4, 21, 1,...   
1392         {605}  [39, 1, 51, 10, 54, 35, 1, 1, 18, 34, 18, 1, 3...   
1393         {239}  [38, 24, 38, 29, 38, 25, 39, 38, 42, 43, 42, 3...   
1394         {314}                                             [1, 1]   

                                          card_identity  
0     [0xB8CD7FA23F5FFE6F983DBC7217E3EA02, 0xD2962BC...  
1     [0x3287C89840AC8E553AC17D38619DB1E7, 0x24E7369...  
2                  [0xA4808717EFB854A085BD3664E19F01DF]  
3     [0x305782BD54FCBB0A043C4C9E4AA01918, 0x3167F75...  
4     [0xE81E0A479902CA839EAB246A94BD9992, 0x17D0E57...  
...                                                 ...  
1390  [0xFA9FCDEAC15446839F72F2763F0DCB29, 0x3979107...  
1391  [0x24CD4BBDA81997D3E1E5554A17F29DD1, 0xA47535B...  
1392  [0x7FB4EBC36F716E8A16C801B2DEE0BC6F, 0x7D27E59...  
1393  [0xECF645F91B08A81A5D0CF1BB42F7FA34, 0xD9645EC...  
1394  [0x609007392BC24C970F159CBFB03EFE33, 0x8172602...  

[1395 rows x 5 columns]

In [11]:
day_0929_bus_info_dataframe['time_station']=day_0929_bus_info_dataframe.apply(lambda x:list(zip(x['custom_precise_time'],x['station_identity'])),axis=1)
day_0929_bus_info_dataframe

car_identity                                custom_precise_time  \
0             3730                               [18:58:34, 18:58:55]   
1             3732  [07:13:16, 10:58:56, 18:55:56, 10:58:52, 15:12...   
2             3734                                         [17:48:18]   
3             3736  [19:08:33, 15:20:00, 18:24:07, 18:39:17, 15:04...   
4             3737  [08:58:42, 16:19:23, 07:25:40, 08:15:17, 08:10...   
...            ...                                                ...   
1390          7800  [08:22:42, 13:06:23, 09:27:01, 15:29:52, 08:55...   
1391          7801  [11:47:57, 09:50:06, 16:30:44, 18:12:36, 11:28...   
1392          7823  [07:37:52, 13:59:52, 13:02:56, 11:42:13, 16:04...   
1393         15019  [09:40:52, 12:26:44, 15:42:05, 12:35:19, 15:42...   
1394        207578                               [11:01:28, 08:08:22]   

     line_identity                                   station_identity  \
0           {4601}                                           [37, 37]   
1            {291}  [9, 19, 55, 19, 33, 32, 36, 45, 53, 3, 38, 3, ...   
2           {4601}                                               [37]   
3            {256}  [22, 45, 1, 7, 41, 11, 3, 10, 47, 4, 58, 58, 2...   
4            {256}  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
...            ...                                                ...   
1390         {602}  [2, 23, 31, 23, 18, 2, 19, 7, 18, 18, 18, 6, 1...   
1391         {602}  [18, 18, 18, 6, 7, 23, 24, 7, 18, 1, 4, 21, 1,...   
1392         {605}  [39, 1, 51, 10, 54, 35, 1, 1, 18, 34, 18, 1, 3...   
1393         {239}  [38, 24, 38, 29, 38, 25, 39, 38, 42, 43, 42, 3...   
1394         {314}                                             [1, 1]   

                                          card_identity  \
0     [0xB8CD7FA23F5FFE6F983DBC7217E3EA02, 0xD2962BC...   
1     [0x3287C89840AC8E553AC17D38619DB1E7, 0x24E7369...   
2                  [0xA4808717EFB854A085BD3664E19F01DF]   
3     [0x305782BD54FCBB0A043C4C9E4AA01918, 0x3167F75...   
4     [0xE81E0A479902CA839EAB246A94BD9992, 0x17D0E57...   
...                                                 ...   
1390  [0xFA9FCDEAC15446839F72F2763F0DCB29, 0x3979107...   
1391  [0x24CD4BBDA81997D3E1E5554A17F29DD1, 0xA47535B...   
1392  [0x7FB4EBC36F716E8A16C801B2DEE0BC6F, 0x7D27E59...   
1393  [0xECF645F91B08A81A5D0CF1BB42F7FA34, 0xD9645EC...   
1394  [0x609007392BC24C970F159CBFB03EFE33, 0x8172602...   

                                           time_station  
0                      [(18:58:34, 37), (18:58:55, 37)]  
1     [(07:13:16, 9), (10:58:56, 19), (18:55:56, 55)...  
2                                      [(17:48:18, 37)]  
3     [(19:08:33, 22), (15:20:00, 45), (18:24:07, 1)...  
4     [(08:58:42, 1), (16:19:23, 1), (07:25:40, 1), ...  
...                                                 ...  
1390  [(08:22:42, 2), (13:06:23, 23), (09:27:01, 31)...  
1391  [(11:47:57, 18), (09:50:06, 18), (16:30:44, 18...  
1392  [(07:37:52, 39), (13:59:52, 1), (13:02:56, 51)...  
1393  [(09:40:52, 38), (12:26:44, 24), (15:42:05, 38...  
1394                     [(11:01:28, 1), (08:08:22, 1)]  

[1395 rows x 6 columns]

In [12]:
day_0929_bus_info_dataframe['sort_time_station']= day_0929_bus_info_dataframe.apply(lambda x:\
                               sorted(x['time_station'],key=lambda y:y[0])\
                               ,axis=1)
day_0929_bus_info_dataframe

car_identity                                custom_precise_time  \
0             3730                               [18:58:34, 18:58:55]   
1             3732  [07:13:16, 10:58:56, 18:55:56, 10:58:52, 15:12...   
2             3734                                         [17:48:18]   
3             3736  [19:08:33, 15:20:00, 18:24:07, 18:39:17, 15:04...   
4             3737  [08:58:42, 16:19:23, 07:25:40, 08:15:17, 08:10...   
...            ...                                                ...   
1390          7800  [08:22:42, 13:06:23, 09:27:01, 15:29:52, 08:55...   
1391          7801  [11:47:57, 09:50:06, 16:30:44, 18:12:36, 11:28...   
1392          7823  [07:37:52, 13:59:52, 13:02:56, 11:42:13, 16:04...   
1393         15019  [09:40:52, 12:26:44, 15:42:05, 12:35:19, 15:42...   
1394        207578                               [11:01:28, 08:08:22]   

     line_identity                                   station_identity  \
0           {4601}                                           [37, 37]   
1            {291}  [9, 19, 55, 19, 33, 32, 36, 45, 53, 3, 38, 3, ...   
2           {4601}                                               [37]   
3            {256}  [22, 45, 1, 7, 41, 11, 3, 10, 47, 4, 58, 58, 2...   
4            {256}  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
...            ...                                                ...   
1390         {602}  [2, 23, 31, 23, 18, 2, 19, 7, 18, 18, 18, 6, 1...   
1391         {602}  [18, 18, 18, 6, 7, 23, 24, 7, 18, 1, 4, 21, 1,...   
1392         {605}  [39, 1, 51, 10, 54, 35, 1, 1, 18, 34, 18, 1, 3...   
1393         {239}  [38, 24, 38, 29, 38, 25, 39, 38, 42, 43, 42, 3...   
1394         {314}                                             [1, 1]   

                                          card_identity  \
0     [0xB8CD7FA23F5FFE6F983DBC7217E3EA02, 0xD2962BC...   
1     [0x3287C89840AC8E553AC17D38619DB1E7, 0x24E7369...   
2                  [0xA4808717EFB854A085BD3664E19F01DF]   
3     [0x305782BD54FCBB0A043C4C9E4AA01918, 0x3167F75...   
4     [0xE81E0A479902CA839EAB246A94BD9992, 0x17D0E57...   
...                                                 ...   
1390  [0xFA9FCDEAC15446839F72F2763F0DCB29, 0x3979107...   
1391  [0x24CD4BBDA81997D3E1E5554A17F29DD1, 0xA47535B...   
1392  [0x7FB4EBC36F716E8A16C801B2DEE0BC6F, 0x7D27E59...   
1393  [0xECF645F91B08A81A5D0CF1BB42F7FA34, 0xD9645EC...   
1394  [0x609007392BC24C970F159CBFB03EFE33, 0x8172602...   

                                           time_station  \
0                      [(18:58:34, 37), (18:58:55, 37)]   
1     [(07:13:16, 9), (10:58:56, 19), (18:55:56, 55)...   
2                                      [(17:48:18, 37)]   
3     [(19:08:33, 22), (15:20:00, 45), (18:24:07, 1)...   
4     [(08:58:42, 1), (16:19:23, 1), (07:25:40, 1), ...   
...                                                 ...   
1390  [(08:22:42, 2), (13:06:23, 23), (09:27:01, 31)...   
1391  [(11:47:57, 18), (09:50:06, 18), (16:30:44, 18...   
1392  [(07:37:52, 39), (13:59:52, 1), (13:02:56, 51)...   
1393  [(09:40:52, 38), (12:26:44, 24), (15:42:05, 38...   
1394                     [(11:01:28, 1), (08:08:22, 1)]   

                                      sort_time_station  
0                      [(18:58:34, 37), (18:58:55, 37)]  
1     [(07:11:31, 8), (07:11:37, 8), (07:11:40, 8), ...  
2                                      [(17:48:18, 37)]  
3     [(13:27:51, 2), (13:28:02, 2), (13:32:01, 3), ...  
4     [(07:07:26, 1), (07:07:30, 1), (07:09:09, 1), ...  
...                                                 ...  
1390  [(06:34:50, 3), (07:10:07, 18), (07:11:16, 1),...  
1391  [(06:24:08, 1), (06:24:13, 1), (06:24:28, 1), ...  
1392  [(07:19:47, 31), (07:19:54, 31), (07:19:55, 31...  
1393  [(09:27:53, 34), (09:31:17, 34), (09:35:34, 37...  
1394                     [(08:08:22, 1), (11:01:28, 1)]  

[1395 rows x 7 columns]

In [13]:
def split_into_groups(data):
    groups = []
    start = 0
    for i in range(1, len(data)):
        if data[i][1] < data[i-1][1]:  # 如果当前元素小于等于前一个元素，说明递增序列断开
            groups.append(data[start:i])
            start = i
    # 添加最后一个分组
    groups.append(data[start:])
    return groups
day_0929_bus_info_dataframe['sort_time_station'] = day_0929_bus_info_dataframe.apply(lambda x:split_into_groups(x['sort_time_station']),axis=1)
day_0929_bus_info_dataframe

car_identity                                custom_precise_time  \
0             3730                               [18:58:34, 18:58:55]   
1             3732  [07:13:16, 10:58:56, 18:55:56, 10:58:52, 15:12...   
2             3734                                         [17:48:18]   
3             3736  [19:08:33, 15:20:00, 18:24:07, 18:39:17, 15:04...   
4             3737  [08:58:42, 16:19:23, 07:25:40, 08:15:17, 08:10...   
...            ...                                                ...   
1390          7800  [08:22:42, 13:06:23, 09:27:01, 15:29:52, 08:55...   
1391          7801  [11:47:57, 09:50:06, 16:30:44, 18:12:36, 11:28...   
1392          7823  [07:37:52, 13:59:52, 13:02:56, 11:42:13, 16:04...   
1393         15019  [09:40:52, 12:26:44, 15:42:05, 12:35:19, 15:42...   
1394        207578                               [11:01:28, 08:08:22]   

     line_identity                                   station_identity  \
0           {4601}                                           [37, 37]   
1            {291}  [9, 19, 55, 19, 33, 32, 36, 45, 53, 3, 38, 3, ...   
2           {4601}                                               [37]   
3            {256}  [22, 45, 1, 7, 41, 11, 3, 10, 47, 4, 58, 58, 2...   
4            {256}  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
...            ...                                                ...   
1390         {602}  [2, 23, 31, 23, 18, 2, 19, 7, 18, 18, 18, 6, 1...   
1391         {602}  [18, 18, 18, 6, 7, 23, 24, 7, 18, 1, 4, 21, 1,...   
1392         {605}  [39, 1, 51, 10, 54, 35, 1, 1, 18, 34, 18, 1, 3...   
1393         {239}  [38, 24, 38, 29, 38, 25, 39, 38, 42, 43, 42, 3...   
1394         {314}                                             [1, 1]   

                                          card_identity  \
0     [0xB8CD7FA23F5FFE6F983DBC7217E3EA02, 0xD2962BC...   
1     [0x3287C89840AC8E553AC17D38619DB1E7, 0x24E7369...   
2                  [0xA4808717EFB854A085BD3664E19F01DF]   
3     [0x305782BD54FCBB0A043C4C9E4AA01918, 0x3167F75...   
4     [0xE81E0A479902CA839EAB246A94BD9992, 0x17D0E57...   
...                                                 ...   
1390  [0xFA9FCDEAC15446839F72F2763F0DCB29, 0x3979107...   
1391  [0x24CD4BBDA81997D3E1E5554A17F29DD1, 0xA47535B...   
1392  [0x7FB4EBC36F716E8A16C801B2DEE0BC6F, 0x7D27E59...   
1393  [0xECF645F91B08A81A5D0CF1BB42F7FA34, 0xD9645EC...   
1394  [0x609007392BC24C970F159CBFB03EFE33, 0x8172602...   

                                           time_station  \
0                      [(18:58:34, 37), (18:58:55, 37)]   
1     [(07:13:16, 9), (10:58:56, 19), (18:55:56, 55)...   
2                                      [(17:48:18, 37)]   
3     [(19:08:33, 22), (15:20:00, 45), (18:24:07, 1)...   
4     [(08:58:42, 1), (16:19:23, 1), (07:25:40, 1), ...   
...                                                 ...   
1390  [(08:22:42, 2), (13:06:23, 23), (09:27:01, 31)...   
1391  [(11:47:57, 18), (09:50:06, 18), (16:30:44, 18...   
1392  [(07:37:52, 39), (13:59:52, 1), (13:02:56, 51)...   
1393  [(09:40:52, 38), (12:26:44, 24), (15:42:05, 38...   
1394                     [(11:01:28, 1), (08:08:22, 1)]   

                                      sort_time_station  
0                    [[(18:58:34, 37), (18:58:55, 37)]]  
1     [[(07:11:31, 8), (07:11:37, 8), (07:11:40, 8),...  
2                                    [[(17:48:18, 37)]]  
3     [[(13:27:51, 2), (13:28:02, 2), (13:32:01, 3),...  
4     [[(07:07:26, 1), (07:07:30, 1), (07:09:09, 1),...  
...                                                 ...  
1390  [[(06:34:50, 3), (07:10:07, 18)], [(07:11:16, ...  
1391  [[(06:24:08, 1), (06:24:13, 1), (06:24:28, 1),...  
1392  [[(07:19:47, 31), (07:19:54, 31), (07:19:55, 3...  
1393  [[(09:27:53, 34), (09:31:17, 34), (09:35:34, 3...  
1394                   [[(08:08:22, 1), (11:01:28, 1)]]  

[1395 rows x 7 columns]

In [14]:
from collections import defaultdict
def split_into_time_dict(data):
    min_times = defaultdict(lambda: '24:24:24')  # 初始化为正无穷大
    # 遍历数据并更新每个站点的最小时间
    for time, station in data:
        if time < min_times[station]:
            min_times[station] = time
    # 将字典中的值转换为列表
    result1 = [(time, station) for station, time in min_times.items()]
    # 根据站点编号排序
    result1.sort(key=lambda x: x[1])
    return result1
day_0929_bus_info_dataframe['remove_dupilicate']=\
    day_0929_bus_info_dataframe.\
        apply(lambda x:\
              [split_into_time_dict(data) for \
               data in x['sort_time_station']],axis=1)
day_0929_bus_info_dataframe

car_identity                                custom_precise_time  \
0             3730                               [18:58:34, 18:58:55]   
1             3732  [07:13:16, 10:58:56, 18:55:56, 10:58:52, 15:12...   
2             3734                                         [17:48:18]   
3             3736  [19:08:33, 15:20:00, 18:24:07, 18:39:17, 15:04...   
4             3737  [08:58:42, 16:19:23, 07:25:40, 08:15:17, 08:10...   
...            ...                                                ...   
1390          7800  [08:22:42, 13:06:23, 09:27:01, 15:29:52, 08:55...   
1391          7801  [11:47:57, 09:50:06, 16:30:44, 18:12:36, 11:28...   
1392          7823  [07:37:52, 13:59:52, 13:02:56, 11:42:13, 16:04...   
1393         15019  [09:40:52, 12:26:44, 15:42:05, 12:35:19, 15:42...   
1394        207578                               [11:01:28, 08:08:22]   

     line_identity                                   station_identity  \
0           {4601}                                           [37, 37]   
1            {291}  [9, 19, 55, 19, 33, 32, 36, 45, 53, 3, 38, 3, ...   
2           {4601}                                               [37]   
3            {256}  [22, 45, 1, 7, 41, 11, 3, 10, 47, 4, 58, 58, 2...   
4            {256}  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
...            ...                                                ...   
1390         {602}  [2, 23, 31, 23, 18, 2, 19, 7, 18, 18, 18, 6, 1...   
1391         {602}  [18, 18, 18, 6, 7, 23, 24, 7, 18, 1, 4, 21, 1,...   
1392         {605}  [39, 1, 51, 10, 54, 35, 1, 1, 18, 34, 18, 1, 3...   
1393         {239}  [38, 24, 38, 29, 38, 25, 39, 38, 42, 43, 42, 3...   
1394         {314}                                             [1, 1]   

                                          card_identity  \
0     [0xB8CD7FA23F5FFE6F983DBC7217E3EA02, 0xD2962BC...   
1     [0x3287C89840AC8E553AC17D38619DB1E7, 0x24E7369...   
2                  [0xA4808717EFB854A085BD3664E19F01DF]   
3     [0x305782BD54FCBB0A043C4C9E4AA01918, 0x3167F75...   
4     [0xE81E0A479902CA839EAB246A94BD9992, 0x17D0E57...   
...                                                 ...   
1390  [0xFA9FCDEAC15446839F72F2763F0DCB29, 0x3979107...   
1391  [0x24CD4BBDA81997D3E1E5554A17F29DD1, 0xA47535B...   
1392  [0x7FB4EBC36F716E8A16C801B2DEE0BC6F, 0x7D27E59...   
1393  [0xECF645F91B08A81A5D0CF1BB42F7FA34, 0xD9645EC...   
1394  [0x609007392BC24C970F159CBFB03EFE33, 0x8172602...   

                                           time_station  \
0                      [(18:58:34, 37), (18:58:55, 37)]   
1     [(07:13:16, 9), (10:58:56, 19), (18:55:56, 55)...   
2                                      [(17:48:18, 37)]   
3     [(19:08:33, 22), (15:20:00, 45), (18:24:07, 1)...   
4     [(08:58:42, 1), (16:19:23, 1), (07:25:40, 1), ...   
...                                                 ...   
1390  [(08:22:42, 2), (13:06:23, 23), (09:27:01, 31)...   
1391  [(11:47:57, 18), (09:50:06, 18), (16:30:44, 18...   
1392  [(07:37:52, 39), (13:59:52, 1), (13:02:56, 51)...   
1393  [(09:40:52, 38), (12:26:44, 24), (15:42:05, 38...   
1394                     [(11:01:28, 1), (08:08:22, 1)]   

                                      sort_time_station  \
0                    [[(18:58:34, 37), (18:58:55, 37)]]   
1     [[(07:11:31, 8), (07:11:37, 8), (07:11:40, 8),...   
2                                    [[(17:48:18, 37)]]   
3     [[(13:27:51, 2), (13:28:02, 2), (13:32:01, 3),...   
4     [[(07:07:26, 1), (07:07:30, 1), (07:09:09, 1),...   
...                                                 ...   
1390  [[(06:34:50, 3), (07:10:07, 18)], [(07:11:16, ...   
1391  [[(06:24:08, 1), (06:24:13, 1), (06:24:28, 1),...   
1392  [[(07:19:47, 31), (07:19:54, 31), (07:19:55, 3...   
1393  [[(09:27:53, 34), (09:31:17, 34), (09:35:34, 3...   
1394                   [[(08:08:22, 1), (11:01:28, 1)]]   

                                      remove_dupilicate  
0                                    [[(18:58:34, 37)]]  
1     [[(

In [15]:
#把每个车的刷卡数据按照时间排序，然后按照递增序列分组，
#然后把每组保留每个站点的第一个数据
#然后根据同样的时间间隔进行填充。
with open('./datas/road_line_station_structure_setting.json', 'r') as f:
    temp_road_line_station_structure_setting = json.load(f)
temp_road_line_station_structure_setting

{'1': {'stations_nums': 20,
  'stations': {'1': '火车站',
   '2': '展览馆',
   '3': '新路口',
   '4': '邮电大楼',
   '5': '大十字',
   '6': '喷水池',
   '7': '云中广场',
   '8': '六广门',
   '9': '北京路',
   '10': '北京西路口',
   '11': '黔灵山公园',
   '12': '黔灵山公园',
   '13': '延安西路',
   '14': '紫林庵',
   '15': '大西门',
   '16': '次南门',
   '17': '河滨公园',
   '18': '新路口',
   '19': '展览馆',
   '20': '火车站'},
  'all_stations': ['火车站',
   '展览馆',
   '新路口',
   '邮电大楼',
   '大十字',
   '喷水池',
   '云中广场',
   '六广门',
   '北京路',
   '北京西路口',
   '黔灵山公园',
   '黔灵山公园',
   '延安西路',
   '紫林庵',
   '大西门',
   '次南门',
   '河滨公园',
   '新路口',
   '展览馆',
   '火车站']},
 '2': {'stations_nums': 20,
  'stations': {'1': '火车站',
   '2': '展览馆',
   '3': '新路口',
   '4': '河滨公园',
   '5': '次南门',
   '6': '大西门',
   '7': '紫林庵',
   '8': '延安西路',
   '9': '黔灵山公园',
   '10': '黔灵山公园',
   '11': '北京西路口',
   '12': '北京路',
   '13': '六广门',
   '14': '云中广场',
   '15': '喷水池',
   '16': '大十字',
   '17': '邮电大楼',
   '18': '新路口',
   '19': '展览馆',
   '20': '火车站'},
  'all_stations': ['火车站',
   '展览馆',
   '新路口',
  

In [16]:
#公交到站时间
buses_2_station_time = {}
arrive_time_2_station_id = {}
for row_index in range(len(day_0929_bus_info_dataframe)):
    #每一行都是一辆车的信息
    row = day_0929_bus_info_dataframe[row_index:row_index+1]
    car_identity = row['car_identity'].values[0]#车牌号
    line_identity = list(row['line_identity'].values[0])[0]#线路名
    remove_dupilicate = row['remove_dupilicate'].values[0]#运行时间表
    #每条线路有哪些站点？
    line_info = temp_road_line_station_structure_setting[str(line_identity)]
    #line_info_stations_nums = line_info['stations_nums']
    line_info_stations_dict = line_info['stations']#线路站点编号到名字的映射
    #这个公交到达各个站点的时间？
    #arrive_time_2_station_id = {}
    #row_station_id_2_arrive_time = {}
    for row_id in range(len(remove_dupilicate)):
        row = remove_dupilicate[row_id]#每一个运行时间表
        temp_arrive_time_2_station_id = dict(zip(line_info_stations_dict.keys(),[None]*len(line_info_stations_dict.keys())))
        for data_instance in row:
            time = data_instance[0]
            station_id = data_instance[1]
            #station_name = line_info_stations_dict[str(station_id)]
            #station_name_2_id = station_2_id[station_name]
            temp_arrive_time_2_station_id[str(station_id)]=time
        if car_identity not in arrive_time_2_station_id:
            arrive_time_2_station_id[car_identity]=[temp_arrive_time_2_station_id]
        else:
            arrive_time_2_station_id[car_identity].append(temp_arrive_time_2_station_id)
arrive_time_2_station_id

{3730: [{'1': None,
   '2': None,
   '3': None,
   '4': None,
   '5': None,
   '6': None,
   '7': None,
   '8': None,
   '9': None,
   '10': None,
   '11': None,
   '12': None,
   '13': None,
   '14': None,
   '15': None,
   '16': None,
   '17': None,
   '18': None,
   '19': None,
   '20': None,
   '21': None,
   '22': None,
   '23': None,
   '24': None,
   '25': None,
   '26': None,
   '27': None,
   '28': None,
   '29': None,
   '30': None,
   '37': '18:58:34'}],
 3732: [{'1': None,
   '2': None,
   '3': None,
   '4': None,
   '5': None,
   '6': None,
   '7': None,
   '8': '07:11:31',
   '9': '07:13:08',
   '10': '07:15:29',
   '11': None,
   '12': '07:16:32',
   '13': None,
   '14': None,
   '15': None,
   '16': None,
   '17': None,
   '18': None,
   '19': None,
   '20': None,
   '21': None,
   '22': None,
   '23': None,
   '24': None,
   '25': None,
   '26': None,
   '27': None,
   '28': None,
   '29': None,
   '30': None,
   '31': None,
   '32': None,
   '33': None,
   '34': None,

In [17]:
# 解析时间列
# 定义一个函数，将 DataFrame 中的时间列解析为时间对象
def parse_time_columns(df):
    for col in df.columns:
        df[col] = pd.to_datetime(df[col], format='%H:%M:%S', errors='coerce').dt.time
    return df

def time_to_seconds(t):
    """将时间对象转换为秒数"""
    if pd.isnull(t):
        return None
    return t.hour * 3600 + t.minute * 60 + t.second
from datetime import datetime, timedelta
def seconds_to_time(s):
    """将秒数转换为时间对象"""
    if pd.isnull(s):
        return None
    return (datetime.min + timedelta(seconds=s)).time()
def fill_weighted_average_updown(df):
    # 对每个空缺值进行处理
    #filled_df = df.copy()
    filled_df = df
    for col in range(len(df.columns)):
        for i in range(len(df)):
            if pd.isnull(df.iloc[i, col]):
                try:
                    non_null_indices = df.iloc[:, col].notnull()
                    up_nonzero = df.iloc[:i, col].notnull().sum()
                    down_nonzero = df.iloc[i+1:, col].notnull().sum()
                    if up_nonzero>0 and down_nonzero >0:
                        #上下平均
                        # 找到前方的最近两个非空值
                        prev_idx = non_null_indices[:i][::-1].idxmax()
                        next_idx = non_null_indices[i:].idxmax()
                        if pd.isnull(prev_idx) or pd.isnull(next_idx):
                            continue
                        prev_time = df.iloc[prev_idx, col]
                        next_time = df.iloc[next_idx, col]
                        # 计算距离
                        distance_prev = i - int(prev_idx)
                        distance_next = int(next_idx) - i
                        prev_time = time_to_seconds(prev_time)
                        next_time = time_to_seconds(next_time)
                        # 计算加权平均
                        filled_time = prev_time + (next_time - prev_time) * (distance_prev / (distance_prev + distance_next))
                        filled_df.iloc[i, col]  = seconds_to_time(filled_time)
                    elif up_nonzero==0 and down_nonzero>1:
                        #下平均
                        # 找到前方的最近两个非空值
                        prev_idx = non_null_indices[i+1:].idxmax()
                        next_idx = non_null_indices[prev_idx+1:].idxmax()
                        if pd.isnull(prev_idx) or pd.isnull(next_idx):
                            continue
                        prev_time = df.iloc[prev_idx, col]
                        next_time = df.iloc[next_idx, col]
                        # 计算距离
                        distance_prev = i - int(prev_idx)
                        distance_next = int(next_idx) - int(prev_idx)
                        prev_time = time_to_seconds(prev_time)
                        next_time = time_to_seconds(next_time)
                        # 计算加权平均
                        filled_time = prev_time + (next_time - prev_time) * (distance_prev / distance_next)
                        filled_df.iloc[i, col]  = seconds_to_time(filled_time)
                    elif up_nonzero>1 and down_nonzero==0:
                        #上平均
                        # 找到前方的最近两个非空值
                        next_idx = non_null_indices[:i][::-1].idxmax()
                        prev_idx = non_null_indices[:next_idx][::-1].idxmax()
                        if pd.isnull(prev_idx) or pd.isnull(next_idx):
                            continue
                        prev_time = df.iloc[prev_idx, col]
                        next_time = df.iloc[next_idx, col]
                        # 计算距离
                        distance_prev = i - int(prev_idx)
                        distance_next = int(next_idx) - int(prev_idx)
                        prev_time = time_to_seconds(prev_time)
                        next_time = time_to_seconds(next_time)
                        # 计算加权平均
                        filled_time = prev_time + (next_time - prev_time) * (distance_prev / distance_next)
                        filled_df.iloc[i, col]  = seconds_to_time(filled_time)
                    elif up_nonzero==0 and down_nonzero==1:
                        # 下平均
                        # 找到前方的最近两个非空值
                        prev_idx = non_null_indices[i+1:].idxmax()#行，i行和prev_idx行
                        column1 = df.iloc[i,:].notnull()
                        column2 = df.iloc[prev_idx,:].notnull()
                        where_column = column1 & column2
                        if sum(where_column[:col])==0 and sum(where_column[col:])==0:
                            continue
                        elif sum(where_column[:col])>0 and sum(where_column[col:])==0:
                            column_prev_idx = where_column[:col][::-1].idxmax()
                            column_next_idx = column_prev_idx
                        else:
                            column_next_idx = where_column[col:].idxmax()
                            column_prev_idx = column_next_idx
                        if pd.isnull(column_prev_idx):
                            prev_prev_time = time_to_seconds(df.loc[prev_idx, column_next_idx])
                            prev_next_time = time_to_seconds(df.iloc[prev_idx, col])
                            this_next_time = time_to_seconds(df.loc[i,column_next_idx])
                        else:
                            prev_prev_time = time_to_seconds(df.loc[prev_idx, column_prev_idx])
                            prev_next_time = time_to_seconds(df.iloc[prev_idx, col])
                            this_next_time = time_to_seconds(df.loc[i,column_prev_idx])
                        # 计算加权平均
                        filled_time = this_next_time + (prev_next_time - prev_prev_time)
                        filled_df.iloc[i, col]  = seconds_to_time(filled_time)
                    elif up_nonzero==1 and down_nonzero==0:
                        # 上平均
                        # 找到前方的最近两个非空值
                        prev_idx = non_null_indices[:i][::-1].idxmax()#行，i行和prev_idx行
                        #where_column = df.iloc[[i,prev_idx],:].notnull()
                        #column_flag = where_column.sum(axis=0)
                        column1 = df.iloc[i,:].notnull()
                        column2 = df.iloc[prev_idx,:].notnull()
                        where_column = column1 & column2
                        if sum(where_column[:col])==0 and sum(where_column[col:])==0:
                            continue
                        elif sum(where_column[:col])>0 and sum(where_column[col:])==0:
                            column_prev_idx = where_column[:col][::-1].idxmax()
                            column_next_idx = column_prev_idx
                        else:
                            column_next_idx = where_column[col:].idxmax()
                            column_prev_idx = column_next_idx
                        
                        if pd.isnull(column_prev_idx):
                            prev_prev_time = time_to_seconds(df.loc[prev_idx, column_next_idx])
                            prev_next_time = time_to_seconds(df.iloc[prev_idx, col])
                            this_next_time = time_to_seconds(df.loc[i,column_next_idx])
                        else:
                            prev_prev_time = time_to_seconds(df.loc[prev_idx, column_prev_idx])
                            prev_next_time = time_to_seconds(df.iloc[prev_idx, col])
                            this_next_time = time_to_seconds(df.loc[i,column_prev_idx])
                        # 计算加权平均
                        filled_time = this_next_time + (prev_next_time - prev_prev_time)
                        filled_df.iloc[i, col]  = seconds_to_time(filled_time)
                    else:
                        continue
                except:
                    continue
    return filled_df
# 应用填充函数到DataFrame的每一行
#中间填充
def fill_weighted_average(row):
    non_null_indices = row.notnull()
    if non_null_indices.sum() < 2:
        return row
    filled_row = row
    #filled_row = row.copy()
    for i in range(len(row)):
        if pd.isnull(row.iloc[i]):
            try:
                # 找到前后的最近非空值
                prev_idx = non_null_indices[:i][::-1].idxmax()
                next_idx = non_null_indices[i:].idxmax()
            
                if pd.isnull(prev_idx) or pd.isnull(next_idx):
                    continue

                prev_time = row[prev_idx]
                next_time = row[next_idx]
            
                # 计算距离
                distance_prev = int(row.keys()[i]) - int(prev_idx)
                distance_next = int(next_idx) - int(row.keys()[i])
                prev_time = time_to_seconds(prev_time)
                next_time = time_to_seconds(next_time)
                # 计算加权平均
                filled_time = prev_time + (next_time - prev_time) * (distance_prev / (distance_prev + distance_next))
            
                filled_row.iloc[i] = seconds_to_time(filled_time)
            except:
                continue
    return filled_row
# 应用填充函数到DataFrame的每一行
#向左填充
def fill_weighted_average_left(row):
    non_null_indices = row.notnull()
    if non_null_indices.sum() < 2:
        return row
    filled_row = row
    #filled_row = row.copy()
    for i in range(len(row)):
        if pd.isnull(row.iloc[i]):
            try:
                # 找到后方的最近两个非空值
                prev_idx = non_null_indices[i+1:].idxmax()
                next_idx = non_null_indices[list(row.keys()).index(prev_idx)+1:].idxmax()
                #row.keys().index(prev_idx)
                #prev_idx = non_null_indices[:i][::-1].idxmax()
                #next_idx = non_null_indices[i:].idxmax()
            
                if pd.isnull(prev_idx) or pd.isnull(next_idx):
                    continue

                prev_time = row[prev_idx]
                next_time = row[next_idx]
            
                # 计算距离
                distance_prev = int(row.keys()[i]) - int(prev_idx)
                distance_next = int(next_idx) - int(prev_idx)
                prev_time = time_to_seconds(prev_time)
                next_time = time_to_seconds(next_time)
                # 计算加权平均
                filled_time = prev_time + (next_time - prev_time) * (distance_prev / distance_next)
            
                filled_row.iloc[i] = seconds_to_time(filled_time)
            except:
                continue
    return filled_row
# 应用填充函数到DataFrame的每一行
#向右填充
def fill_weighted_average_right(row):
    non_null_indices = row.notnull()
    if non_null_indices.sum() < 2:
        return row
    filled_row = row
    #filled_row = row.copy()
    for i in range(len(row)):
        if pd.isnull(row.iloc[i]):
            try:
                # 找到前方的最近两个非空值
                next_idx = non_null_indices[:i][::-1].idxmax()
                prev_idx = non_null_indices[:list(row.keys()).index(next_idx)][::-1].idxmax()
            
                if pd.isnull(prev_idx) or pd.isnull(next_idx):
                    continue

                prev_time = row[prev_idx]
                next_time = row[next_idx]
            
                # 计算距离
                distance_prev = int(row.keys()[i]) - int(prev_idx)
                distance_next = int(next_idx) - int(prev_idx)
                prev_time = time_to_seconds(prev_time)
                next_time = time_to_seconds(next_time)
                # 计算加权平均
                filled_time = prev_time + (next_time - prev_time) * (distance_prev / distance_next)
            
                filled_row.iloc[i] = seconds_to_time(filled_time)
            except:
                continue
    return filled_row
# 应用填充函数到DataFrame的每一行


In [18]:
import concurrent.futures
import time
def process_dataframe(key, df):
    start_time = time.time()
    df = pd.DataFrame(df)
    temp = parse_time_columns(df)
    temp = fill_weighted_average_updown(temp)
    temp = temp.apply(fill_weighted_average, axis=1)
    temp = temp.apply(fill_weighted_average_left, axis=1)
    temp = temp.apply(fill_weighted_average_right, axis=1)
    end_time = time.time()
    return key, temp, end_time-start_time
# 并行处理字典中的每个 DataFrame
process_time_dict = {}
with concurrent.futures.ThreadPoolExecutor() as executor:
    futures = {executor.submit(process_dataframe, key, arrive_time_2_station_id[key]): key for key in arrive_time_2_station_id.keys()}
    for future in concurrent.futures.as_completed(futures):
        key, result_df,process_time = future.result()
        arrive_time_2_station_id[key] = result_df
        process_time_dict[key] = process_time
process_time_dict

{3788: 0.690662145614624,
 3734: 0.13285565376281738,
 3730: 0.07010650634765625,
 3755: 4.289565563201904,
 3756: 4.4864606857299805,
 3762: 1.4372639656066895,
 3760: 1.598198652267456,
 3737: 2.014547109603882,
 3771: 4.687175989151001,
 3776: 4.649056911468506,
 3786: 5.148582696914673,
 3736: 8.295586824417114,
 3796: 3.6369385719299316,
 3774: 8.432820320129395,
 3751: 11.69031023979187,
 3738: 12.50442910194397,
 3790: 8.678181886672974,
 3763: 11.496062755584717,
 3789: 9.202797412872314,
 3759: 12.481612920761108,
 3769: 11.651485919952393,
 3787: 10.42979907989502,
 3783: 11.3981454372406,
 3750: 14.61567211151123,
 3761: 13.963595867156982,
 3782: 12.245005130767822,
 3764: 13.73234748840332,
 3792: 10.792111873626709,
 3793: 10.569014549255371,
 3748: 17.310481309890747,
 3781: 15.644573450088501,
 3830: 3.4132397174835205,
 3822: 5.723094701766968,
 3757: 19.006499528884888,
 3794: 14.696396112442017,
 3772: 18.43559432029724,
 3805: 10.253930568695068,
 3799: 12.713221549

In [21]:
total_time = 0
total_time_list =[]
for key,item in process_time_dict.items():
    total_time += item
    total_time_list.append(item)
print(total_time)

12291.960430145264


In [ ]:
#有了时间表了，该怎么根据时间切片呢？
#换言之，输入一个时间该怎么查询公交车到那个节点了？
#除了识别出公交的位置后，还需要定义各个节点的发出流量，各个时刻的发出流量。方便做仿真
#可以动态监控路段中的流量。
#我们知道了车的运行时间表，该怎么知道车上有哪些乘客呢？
#乘客我们知道了出发时间和出发方向，以及选择的路线等信息。
#那么可以知道他乘坐的是哪辆车。选择最近的乘坐。
#创建用户？


In [61]:
card_info_dataframe
#找到线路与公交的关系。
#各趟公交的出发和到站时间关系。
day_0929_line_car_dataframe = day_0929_dataframe.groupby('line_identity').\
    agg({'car_identity':set},axis=1).reset_index()
day_0929_line_car_dataframe['car_identity'] = \
    day_0929_line_car_dataframe.apply(lambda x:list(x['car_identity']),axis=1)
day_0929_line_car_dataframe

line_identity                                       car_identity
0                0                                                [0]
1                1  [4654, 4655, 4656, 4657, 4659, 4660, 4661, 466...
2                2  [4672, 4673, 4675, 4676, 4679, 4681, 4683, 468...
3                3  [7265, 7333, 7274, 7339, 3854, 7536, 7537, 735...
4                4  [4288, 4289, 4290, 4292, 4293, 4294, 4295, 428...
..             ...                                                ...
242           8259         [4145, 4146, 4147, 4148, 4149, 4150, 4151]
243           8262               [4107, 4108, 4109, 4112, 4113, 4114]
244           8267               [4045, 4154, 4155, 4156, 4157, 4158]
245           8292  [4160, 4075, 4076, 4078, 4082, 4083, 4057, 405...
246           9001                                             [5177]

[247 rows x 2 columns]

In [64]:
line_2_buses = {}
for row_index in range(len(day_0929_line_car_dataframe)):
    row = day_0929_line_car_dataframe[row_index:row_index+1]
    line_identity = row['line_identity'].values[0]
    car_identity = row['car_identity'].values[0]
    line_2_buses[line_identity] = car_identity
line_2_buses

{0: [0],
 1: [4654, 4655, 4656, 4657, 4659, 4660, 4661, 4662, 4665, 4666, 4670],
 2: [4672, 4673, 4675, 4676, 4679, 4681, 4683, 4684, 4685, 4686, 4687],
 3: [7265, 7333, 7274, 7339, 3854, 7536, 7537, 7356, 7539, 7477, 7260, 7358],
 4: [4288, 4289, 4290, 4292, 4293, 4294, 4295, 4286, 4287],
 5: [4782, 4783, 4784, 4785, 4786, 4787, 4788, 4789, 4790, 4791, 4792],
 6: [7424, 7744, 7783, 3978, 7538, 7442, 4031, 7741, 7742, 7743],
 7: [5017,
  7535,
  5015,
  5011,
  5012,
  5013,
  5014,
  5080,
  5016,
  5081,
  5018,
  5019,
  5020],
 8: [4871, 4872, 4873, 4874, 4875, 4877, 4878, 4880],
 9: [3876, 3877, 3878, 3882, 3885, 3886, 3887, 3889, 3890, 3893, 3895, 3896],
 10: [4692, 4693, 4694, 4695, 4696, 4697, 4698, 4699, 4700, 4701],
 11: [4029, 4020, 4021, 4022, 4025, 4026, 4027, 3804, 3805, 4030],
 12: [4704, 4705, 4706, 4707, 4708, 4709, 4710, 7303, 4712, 4713],
 13: [7616, 7618, 7559, 7629, 7573, 6614, 6935, 7066, 7067],
 14: [5120, 5122, 5123, 5124, 5116, 5117, 5119],
 15: [5030, 5031, 50